<h1 style="text-align:center;">Clustering via DBSCAN Algorithm</h1>
<p style="text-align:center;">
Nazar Khan
<br>CVML Lab
<br>University of The Punjab
</p>

This tutorial explains the **Density-Based Spatial Clustering of Applications with Noise (DBSCAN)** algorithm. We’ll implement it from scratch and demonstrate its behavior visually to make the concepts clear.

---

### **1. What is DBSCAN?**

**DBSCAN** is a clustering algorithm that groups points based on their density. Unlike K-means, it does not require the number of clusters beforehand.

Key concepts:
- **Core Points**: Points with at least $minPts$ neighbors within a given distance $\varepsilon$.
- **Border Points**: Points that are not core points but fall within the $\varepsilon$-neighborhood of a core point.
- **Noise Points**: Points that are neither core nor border points.

---

### **2. Install Required Libraries**
Install necessary libraries for plotting and computation:
```bash
pip install numpy matplotlib
```

---

### **3. Imports**

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from collections import deque


---

### **4. Visual Helper Functions**
We’ll write helper functions to visualize points, clusters, and steps of DBSCAN.

In [ ]:
def plot_points(data, labels=None, title="DBSCAN Clustering", core_samples=None):
    plt.figure(figsize=(8, 6))
    unique_labels = set(labels) if labels is not None else [-1]
    
    colors = plt.cm.Spectral(np.linspace(0, 1, len(unique_labels)))
    
    for label, color in zip(unique_labels, colors):
        if label == -1:
            color = [0, 0, 0, 0.5]  # Black for noise
        
        # Select points with the current label
        points = data[labels == label]
        plt.scatter(points[:, 0], points[:, 1], c=[color], s=50, label=f"Cluster {label}" if label != -1 else "Noise")
    
    if core_samples is not None:
        plt.scatter(core_samples[:, 0], core_samples[:, 1], c='yellow', edgecolors='k', s=100, label="Core Points")
    
    plt.title(title)
    plt.legend()
    plt.show()

---

### **5. Distance Calculation**
We need a function to compute the Euclidean distance between two points.

In [ ]:
def euclidean_distance(p1, p2):
    return np.sqrt(np.sum((p1 - p2) ** 2))

---

### **6. DBSCAN Implementation**

Here’s the full implementation of DBSCAN.

In [ ]:
def dbscan(data, eps, min_pts):
    """
    DBSCAN implementation.
    Parameters:
        data: ndarray - Input data points (NxM).
        eps: float - Radius of neighborhood.
        min_pts: int - Minimum number of points to form a dense region.
    Returns:
        labels: list - Cluster labels for each point (-1 means noise).
    """
    labels = np.full(len(data), -1)  # Initialize all points as noise (-1)
    cluster_id = 0  # Start cluster IDs
    
    def region_query(point_idx):
        """Find all neighbors of a point within radius eps."""
        neighbors = []
        for i in range(len(data)):
            if euclidean_distance(data[point_idx], data[i]) <= eps:
                neighbors.append(i)
        return neighbors
    
    def expand_cluster(point_idx, neighbors):
        """Expand cluster for a core point."""
        labels[point_idx] = cluster_id
        queue = deque(neighbors)  # Use a queue to process all neighbors
        
        while queue:
            neighbor_idx = queue.popleft()
            
            if labels[neighbor_idx] == -1:  # Previously labeled as noise, now a border point
                labels[neighbor_idx] = cluster_id
                
            if labels[neighbor_idx] == -1 or labels[neighbor_idx] == 0:
                labels[neighbor_idx] = cluster_id
                new_neighbors = region_query(neighbor_idx)
                if len(new_neighbors) >= min_pts:  # If it's a core point, expand further
                    queue.extend(new_neighbors)
    
    for i in range(len(data)):
        if labels[i] != -1:  # Skip already processed points
            continue
        
        neighbors = region_query(i)  # Find neighbors
        if len(neighbors) < min_pts:
            labels[i] = -1  # Noise
        else:
            cluster_id += 1
            expand_cluster(i, neighbors)
    
    return labels

---

### **7. Visual Demonstration**

We’ll generate synthetic 2D data to demonstrate DBSCAN.

#### Generate Data:

In [ ]:
from sklearn.datasets import make_moons, make_blobs

# Generate synthetic data: moons + random noise
data, _ = make_moons(n_samples=300, noise=0.07, random_state=42)
plt.scatter(data[:, 0], data[:, 1], s=50)
plt.title("Raw Data")
plt.show()

---

#### Run DBSCAN and Visualize:

In [ ]:
# DBSCAN parameters
eps = 0.2
min_pts = 5

# Run DBSCAN
labels = dbscan(data, eps, min_pts)

# Find core points (optional, for visualization)
unique_labels = set(labels)
core_samples = np.array([data[i] for i in range(len(data)) if len([j for j in range(len(data)) if euclidean_distance(data[i], data[j]) <= eps]) >= min_pts])

# Visualize clusters
plot_points(data, labels=np.array(labels), title="DBSCAN Clustering Results", core_samples=core_samples)

---

### **8. Step-by-Step Understanding with Visualization**

To show **intermediate results**, adjust `plot_points` calls inside the `expand_cluster` function to visualize:
- Points being processed.
- Clusters expanding step-by-step.

---

### **9. Key Parameters**
- **$\varepsilon$ (eps)**: Radius of the neighborhood.
- **$minPts$**: Minimum points required to form a dense region.

---

### **10. Advantages of DBSCAN**
1. Does not require the number of clusters $K$ as input.
2. Handles arbitrary cluster shapes.
3. Identifies noise points.

### **11. Disadvantages of DBSCAN**
1. Performance may suffer in high dimensions.
2. Sensitive to $\varepsilon$ and $minPts$.

---

### **Output**
1. **Raw Data Visualization**:
   - Randomly scattered points (e.g., moons).
2. **Clustered Output**:
   - Points assigned to clusters.
   - Noise points marked in black.

---

### **Exercises**
1. Experiment with $\varepsilon$ and $minPts$ values to observe changes in clustering.
2. Use other synthetic datasets like `make_blobs`.
3. Visualize step-by-step expansion of clusters for better understanding.

This tutorial provides an intuitive understanding of DBSCAN with clear code and visual examples.